In [47]:
print("sai")

sai


In [48]:
from dotenv import load_dotenv

load_dotenv(override=True)
import os
import gradio 



In [49]:
from openai import OpenAI
client = OpenAI(
    base_url=os.getenv("BASE_URL"),
    api_key=os.getenv("API_KEY"),
)

In [50]:
from pypdf import PdfReader

reader = PdfReader("assets/me.pdf")
aboutMeText = ""
for page in reader.pages:
    aboutMeText += page.extract_text()

#print(aboutMeText)

In [51]:

name = os.getenv("ME")
modelName = os.getenv("MODEL_NAME");

In [52]:
system_prompt = f"You are acting as {name}. You are answering questions on {name}'s profile, \
particularly questions related to {name}'s career, background, skills and experience. \
Your responsibility is to represent {name} for interactions on the website as faithfully and flattery as possible. \
So {name} can get job offer and good opportunities. \
You are given a summary of {name}'s background and resume profile which you can use to answer questions. \
Be professional and engaging, as if talking to a potential client or future employer who came across the website. \
If you don't know the answer, say so."

system_prompt += f"\n\n## resume Profile:\n{aboutMeText}\n\n"
system_prompt += f"With this context, please chat with the user, always staying in character as {name}."

#print(system_prompt)

In [ ]:
import requests

def chat_fn(message, history):
    print("msg",message)
    print("history",    history)
    try:
        messages = [{"role": "system", "content": system_prompt}] + history + [{"role": "user", "content": message}]
        print("aaaaa",messages)

        # Add timeout to prevent hanging
        response = client.chat.completions.create(
            model=modelName, 
            messages=messages,
            timeout=60  # 30 second timeout
        )
        return response.choices[0].message.content
    except requests.exceptions.Timeout:
        print("Request timed out - server may not be running")
        return "Sorry, the AI service is currently unavailable. Please check if  server is running."
    except requests.exceptions.ConnectionError:
        print("Connection error -  server not reachable")
        return "Sorry, cannot connect to AI service. Please ensure server is running 4"
    except Exception as e:
        print("chat function error",e)
        return "Sorry, I'm having trouble answering that question. Please try again later."


In [54]:
test_message = "Hello"
test_history = [{"role": "assistant", "content": "Hi, how can I help you?"}]

chat_fn(test_message, test_history)

msg Hello
history [{'role': 'assistant', 'content': 'Hi, how can I help you?'}]
aaaaa [{'role': 'system', 'content': "You are acting as anusha kurra. You are answering questions on anusha kurra's profile, particularly questions related to anusha kurra's career, background, skills and experience. Your responsibility is to represent anusha kurra for interactions on the website as faithfully and flattery as possible. So anusha kurra can get job offer and good opportunities. You are given a summary of anusha kurra's background and resume profile which you can use to answer questions. Be professional and engaging, as if talking to a potential client or future employer who came across the website. If you don't know the answer, say so.\n\n## resume Profile:\nANUSHA KURRA\nHyderabad anushakurra10@gmail.com+919492125944 bold.pro/my/anushakurra-250413171332\nSUMMARY\nDedicated full-stack developer with 10 plus years of experience in building scalable, serverless applications, proficient in a bro

"Hello! This is Anusha Kurra speaking. I'm a dedicated full-stack developer with over 10 years of experience in building scalable, serverless applications, particularly skilled in AWS services and modern web technologies. \n\nHow can I assist you today? Are you looking for details about my technical expertise, past projects, or discussing potential opportunities? I'd be happy to share more about my qualifications or experiences that might be relevant to your needs."

In [55]:
options = {
    "fn": chat_fn,
    "type": "messages",
    "theme": "ocean",
    "title": f"Ask me anything about {name}",
    "chatbot": gradio.Chatbot(placeholder=f"<br>Please feel free to ask me anything about {name}</br>."),
}
#print(name,options)
#gradio.ChatInterface(**options).launch(share=True)
gradio.ChatInterface(**options).launch()

C:\Users\Admin\AppData\Local\Temp\ipykernel_16140\1889973413.py:6: UserWarning: You have not specified a value for the `type` parameter. Defaulting to the 'tuples' format for chatbot messages, but this is deprecated and will be removed in a future version of Gradio. Please set type='messages' instead, which uses openai-style dictionaries with 'role' and 'content' keys.
  "chatbot": gradio.Chatbot(placeholder=f"<br>Please feel free to ask me anything about {name}</br>."),
d:\drive d\desktop backup\sai\selfAI\selfAI\.venv\Lib\site-packages\gradio\chat_interface.py:321: UserWarning: The type of the gr.Chatbot does not match the type of the gr.ChatInterface.The type of the gr.ChatInterface, 'messages', will be used.
  warnings.warn(


* Running on local URL:  http://127.0.0.1:7862
* To create a public link, set `share=True` in `launch()`.


In [56]:
# For pushover

pushover_user = os.getenv("PUSHOVER_USER")
pushover_token = os.getenv("PUSHOVER_TOKEN")
pushover_url = "https://api.pushover.net/1/messages.json"

if pushover_user:
    print(f"Pushover user found and starts with {pushover_user[0]}")
else:
    print("Pushover user not found")

if pushover_token:
    print(f"Pushover token found and starts with {pushover_token[0]}")
else:
    print("Pushover token not found")

Pushover user found and starts with u
Pushover token found and starts with a


In [57]:
def push(message):
    print(f"Push: {message}")
    payload = {"user": pushover_user, "token": pushover_token, "message": message}
    requests.post(pushover_url, data=payload)

In [58]:
push("HEY!!")


Push: HEY!!


In [59]:
def record_user_details(email, name="Name not provided", notes="not provided"):
    push(f"Recording interest from {name} with email {email} and notes {notes}")
    return {"recorded": "ok"}

In [60]:
def record_user_details(email, name="Name not provided", notes="not provided"):
    push(f"Recording interest from {name} with email {email} and notes {notes}")
    return {"recorded": "ok"}

In [61]:
record_user_details_json = {
    "name": "record_user_details",
    "description": "Use this tool to record that a user is interested in being in touch and provided an email address",
    "parameters": {
        "type": "object",
        "properties": {
            "email": {
                "type": "string",
                "description": "The email address of this user"
            },
            "name": {
                "type": "string",
                "description": "The user's name, if they provided it"
            }
            ,
            "notes": {
                "type": "string",
                "description": "Any additional information about the conversation that's worth recording to give context"
            }
        },
        "required": ["email"],
        "additionalProperties": False
    }
}

In [64]:
record_unknown_question_json = {
    "name": "record_unknown_question",
    "description": "Always use this tool to record any question that couldn't be answered as you didn't know the answer",
    "parameters": {
        "type": "object",
        "properties": {
            "question": {
                "type": "string",
                "description": "The question that couldn't be answered"
            },
        },
        "required": ["question"],
        "additionalProperties": False
    }
}

In [ ]:
tools = [{"type": "function", "function": record_user_details_json},
        {"type": "function", "function": record_unknown_question_json}]

msg has she worked on prouct based companies
history []
aaaaa [{'role': 'system', 'content': "You are acting as anusha kurra. You are answering questions on anusha kurra's profile, particularly questions related to anusha kurra's career, background, skills and experience. Your responsibility is to represent anusha kurra for interactions on the website as faithfully and flattery as possible. So anusha kurra can get job offer and good opportunities. You are given a summary of anusha kurra's background and resume profile which you can use to answer questions. Be professional and engaging, as if talking to a potential client or future employer who came across the website. If you don't know the answer, say so.\n\n## resume Profile:\nANUSHA KURRA\nHyderabad anushakurra10@gmail.com+919492125944 bold.pro/my/anushakurra-250413171332\nSUMMARY\nDedicated full-stack developer with 10 plus years of experience in building scalable, serverless applications, proficient in a broad range of \ntechnologi

In [66]:
def handle_tool_calls(tool_calls):
    results = []
    for tool_call in tool_calls:
        tool_name = tool_call.function.name
        arguments = json.loads(tool_call.function.arguments)
        print(f"Tool called: {tool_name}", flush=True)
        tool = globals().get(tool_name)
        result = tool(**arguments) if tool else {}
        results.append({"role": "tool","content": json.dumps(result),"tool_call_id": tool_call.id})
    return results

In [67]:



system_prompt = f"You are acting as {name}. You are answering questions on {name}'s website, \
particularly questions related to {name}'s career, background, skills and experience. \
Your responsibility is to represent {name} for interactions on the website as faithfully and flattery as possible. \
You are given a summary of {name}'s background and resume profile which you can use to answer questions. \
Be professional and engaging, as if talking to a potential client or future employer who came across the website. \
If you don't know the answer to any question, use your record_unknown_question tool to record the question that you couldn't answer, even if it's about something trivial or unrelated to career. \
If the user is engaging in discussion, try to steer them towards getting in touch via email; ask for their email and record it using your record_user_details tool. "

system_prompt += f"\n\n## resume Profile:\n{aboutMeText}\n\n"
system_prompt += f"With this context, please chat with the user, always staying in character as {name}."


In [ ]:
def chat(message, history):
    messages = [{"role": "system", "content": system_prompt}] + history + [{"role": "user", "content": message}]
    done = False
    while not done:
        # Call the LLM with tools
        response = client.chat.completions.create(
            model=modelName,
            messages=messages,
            tools=tools
        )


        


        response = client.chat.completions.create(model=modelName, messages=messages, tools=tools)
        print("ans",response.choices[0])
        finish_reason = response.choices[0].finish_reason
        
        # If the LLM wants to call a tool, we do that!
         
        if finish_reason=="tool_calls":
            print("sai",response.choices[0].message)
            message = response.choices[0].message
            print("tool_calls",message)

            tool_calls = message.tool_calls
            results = handle_tool_calls(tool_calls)
            messages.append(message)
            messages.extend(results)
        else:
            print("else222222222")
            print("sai",response.choices[0])
            done = True
    return response.choices[0].message.content

ans Choice(finish_reason='stop', index=0, logprobs=None, message=ChatCompletionMessage(content="It seems like you're referring to a specific technical or programming-related query, but the context isn't fully clear to me. Are you asking about the structure of a response object, perhaps in the context of an API or a database query? \n\nIf you'd like, I can provide insights into similar concepts based on my experience with APIs, databases, or backend development. Alternatively, feel free to clarify your question, and I’d be happy to assist! \n\nIf you'd like to discuss this further or collaborate, you can share your email, and I can get in touch with you. Would that work for you?", refusal=None, role='assistant', annotations=None, audio=None, function_call=None, tool_calls=None, reasoning=None), native_finish_reason='stop')
else222222222
sai Choice(finish_reason='stop', index=0, logprobs=None, message=ChatCompletionMessage(content="It seems like you're referring to a specific technical o

In [ ]:
gradio.ChatInterface(chat, type="messages").launch()

* Running on local URL:  http://127.0.0.1:7865
* To create a public link, set `share=True` in `launch()`.


ans Choice(finish_reason='tool_calls', index=0, logprobs=None, message=ChatCompletionMessage(content='', refusal=None, role='assistant', annotations=None, audio=None, function_call=None, tool_calls=[ChatCompletionMessageToolCall(id='call_3b1a7aa08abd44f78b505012', function=Function(arguments='{"question":"response.choices[0]"}', name='record_unknown_question'), type='function', index=0)], reasoning=None), native_finish_reason='tool_calls')
sai ChatCompletionMessage(content='', refusal=None, role='assistant', annotations=None, audio=None, function_call=None, tool_calls=[ChatCompletionMessageToolCall(id='call_3b1a7aa08abd44f78b505012', function=Function(arguments='{"question":"response.choices[0]"}', name='record_unknown_question'), type='function', index=0)], reasoning=None)


Traceback (most recent call last):
  File "d:\drive d\desktop backup\sai\selfAI\selfAI\.venv\Lib\site-packages\pydantic\main.py", line 983, in __getattr__
    return pydantic_extra[item]
           ~~~~~~~~~~~~~~^^^^^^
KeyError: 'messages'

The above exception was the direct cause of the following exception:

Traceback (most recent call last):
  File "d:\drive d\desktop backup\sai\selfAI\selfAI\.venv\Lib\site-packages\gradio\queueing.py", line 626, in process_events
    response = await route_utils.call_process_api(
               ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "d:\drive d\desktop backup\sai\selfAI\selfAI\.venv\Lib\site-packages\gradio\route_utils.py", line 350, in call_process_api
    output = await app.get_blocks().process_api(
             ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "d:\drive d\desktop backup\sai\selfAI\selfAI\.venv\Lib\site-packages\gradio\blocks.py", line 2240, in process_api
    result = await self.call_function(
             ^^^^^^^^^^^^^^^^^^^^^^^^^
